In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
!pip install optuna optuna-dashboard
!pip install git+https://github.com/R-N/ml-utility-loss
!pip install git+https://github.com/R-N/ml-utility-loss --force-reinstall --no-deps

  Cloning https://github.com/R-N/ml-utility-loss to /tmp/pip-req-build-huzgynqm
  Running command git clone --filter=blob:none --quiet https://github.com/R-N/ml-utility-loss /tmp/pip-req-build-huzgynqm
  Resolved https://github.com/R-N/ml-utility-loss to commit 999fa9d4bdbb358553011a9c2171aded09814fc4
  Preparing metadata (setup.py) ... done
  Cloning https://github.com/R-N/ml-utility-loss to /tmp/pip-req-build-yspnsuf0
  Running command git clone --filter=blob:none --quiet https://github.com/R-N/ml-utility-loss /tmp/pip-req-build-yspnsuf0
  Resolved https://github.com/R-N/ml-utility-loss to commit 999fa9d4bdbb358553011a9c2171aded09814fc4
  Preparing metadata (setup.py) ... done
  Created wheel for ml-utility-loss: filename=ml_utility_loss-0.1.1-py3-none-any.whl size=377794 sha256=7a664c2bcb3f0a7a226cb81c9c0b40b83e9f6c8c57a8062fb09e86f9acf2c5ac
  Stored in directory: /tmp/pip-ephem-wheel-cache-v_yffpto/wheels/54/30/38/31c28079b5f07b6c793211d38f72e7f0be6764bfdfe016df74
Successfully buil

In [3]:
%cd /content
!curl -Ls https://github.com/ekzhang/bore/releases/download/v0.4.0/bore-v0.4.0-x86_64-unknown-linux-musl.tar.gz | tar zx -C /usr/bin
!curl -Lo /usr/bin/cloudflared https://github.com/cloudflare/cloudflared/releases/latest/download/cloudflared-linux-amd64 && chmod +x /usr/bin/cloudflared

/content
  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
  0     0    0     0    0     0      0      0 --:--:-- --:--:-- --:--:--     0
  0     0    0     0    0     0      0      0 --:--:-- --:--:-- --:--:--     0
100 34.7M  100 34.7M    0     0  16.1M      0  0:00:02  0:00:02 --:--:-- 30.5M


In [4]:
%cd /content
!rm -rf ml-utility-loss
!git clone https://github.com/R-N/ml-utility-loss
%cd ml-utility-loss
!rm -rf ml_utility_loss

/content
Cloning into 'ml-utility-loss'...
remote: Enumerating objects: 54414, done.
remote: Counting objects: 100% (7327/7327), done.
remote: Compressing objects: 100% (3252/3252), done.
remote: Total 54414 (delta 4134), reused 7251 (delta 4059), pack-reused 47087
Receiving objects: 100% (54414/54414), 239.42 MiB | 10.53 MiB/s, done.
Resolving deltas: 100% (6182/6182), done.
Updating files: 100% (50325/50325), done.
/content/ml-utility-loss


In [5]:
datasets = [
    "insurance",
    "treatment",
    "contraceptive"
]

model_dir = "/content/drive/MyDrive/rizqinur2010/Documents/ITS/Tesis/Model/"

In [24]:
import pandas as pd
import numpy as np
import json
import os

dataset_dir = "datasets"
dataset_name = "insurance"

df = pd.read_csv(os.path.join(dataset_dir, f"{dataset_name}.csv"))
with open(os.path.join(dataset_dir, f"{dataset_name}.json")) as f:
    info = json.load(f)

In [25]:
from ml_utility_loss.util import split_df_ratio

task = info["task"]
target = info["target"]
cat_features = info["cat_features"]
mixed_features = info["mixed_features"]
longtail_features = info["longtail_features"]
integer_features = info["integer_features"]

dfs = {
    "df": df,
}
dfs_test = {}
for i in range(5):
    train, test = split_df_ratio(df, ratio=0.2, i=i, seed=42)
    dfs[i] = train
    dfs_test[i] = test


In [54]:
from ml_utility_loss.util import mkdir

model_name = "lct_gan"
df_name = "df"
#model_name_2 = f"{model_name}_{dataset_name}_{df_name}"
model_dir_2 = os.path.join(model_dir, model_name, dataset_name, str(df_name))
mkdir(model_dir_2)
model_path = os.path.join(model_dir_2, f"model.pt")
g_state_path = os.path.join(model_dir_2, f"g_state.json")
d_state_path = os.path.join(model_dir_2, f"d_state.json")
params_path = os.path.join(model_dir_2, f"params.json")

In [55]:
print(model_path)

/content/drive/MyDrive/rizqinur2010/Documents/ITS/Tesis/Model/lct_gan/insurance/df/model.pt


In [56]:
import torch

ae_model_dir = "models"
ae_model_name = "lct_ae"
ae_df_name = df_name
ae_model_dir_2 = os.path.join(model_dir, ae_model_name, dataset_name, str(ae_df_name))
ae_model_path = os.path.join(ae_model_dir_2, f"model.pt")
ae_state_path = os.path.join(ae_model_dir_2, f"state.json")
ae_params_path = os.path.join(ae_model_dir_2, f"params.json")

lct_ae = torch.load(ae_model_path)

In [57]:

from ml_utility_loss.tuning import create_objective
import ml_utility_loss.synthesizers.lct_gan.params as PARAMS
from ml_utility_loss.util import filter_dict_2

params = getattr(PARAMS, dataset_name).BEST
gan_params = filter_dict_2(params, PARAMS.default.GAN_PARAMS)

model_params={
    **gan_params,
}

In [51]:
from ml_utility_loss.synthesizers.lct_gan.pipeline import create_gan

gan, synth_df = create_gan(
    lct_ae,
    dfs[df_name],
    **model_params
)

  0%|          | 2/988 [00:00<01:49,  9.00it/s]

[Epoch 1/988] [D loss: -0.001967] [G loss: -0.487792]
[Epoch 2/988] [D loss: -0.002800] [G loss: -0.487687]


  0%|          | 4/988 [00:00<02:27,  6.68it/s]

[Epoch 3/988] [D loss: -0.004177] [G loss: -0.487615]
[Epoch 4/988] [D loss: -0.006083] [G loss: -0.487512]


  1%|          | 6/988 [00:00<02:37,  6.25it/s]

...

[Epoch 985/988] [D loss: -0.967377] [G loss: -0.014141]
[Epoch 986/988] [D loss: -0.964256] [G loss: -0.013743]


100%|██████████| 988/988 [02:25<00:00,  6.77it/s]


[Epoch 987/988] [D loss: -0.962006] [G loss: -0.013196]
[Epoch 988/988] [D loss: -0.962739] [G loss: -0.016487]
Number of steps: 2


100%|██████████| 2/2 [00:00<00:00, 17.01it/s]


Sampled data length 2048


In [52]:
import torch
from copy import deepcopy
import json

!rm -rf params_path
!rm -rf model_path
!rm -rf g_state_path
!rm -rf d_state_path
torch.save(gan, model_path)
torch.save(deepcopy(gan.generator.state_dict()), g_state_path)
torch.save(deepcopy(gan.discriminator.state_dict()), d_state_path)
with open(params_path, "w") as f:
    json.dump(model_params, f, indent=4)

In [53]:
synth_path = os.path.join(model_dir_2, f"synth.csv")
train_path = os.path.join(model_dir_2, f"train.csv")
val_path = os.path.join(model_dir_2, f"val.csv")
test_path = os.path.join(model_dir_2, f"test.csv")

synth_df.to_csv(synth_path)
dfs[df_name].to_csv(train_path)
dfs_test[df_name].to_csv(val_path)
dfs_test[df_name].to_csv(test_path)